# Evaluate trained PINN models

In [9]:
import numpy as np
import torch.nn as nn
import torch
import scipy
import matplotlib.pyplot as plt
import matplotlib.animation as animation

from src.model import NavierStokesPINN1, NavierStokesPINNLoss1
from src.model import NavierStokesPINN2, NavierStokesPINNLoss2
from src.load_cynlinder_wake import load_cylinder_wake

In [10]:
# Load flattened cynlinder wake data
x_all, y_all, t_all, u_all, v_all, p_all, (N, T) = load_cylinder_wake() # (NT, 1)

# Separate N and T dimensions
XX = x_all.reshape(N, T)
YY = y_all.reshape(N, T)
TT = t_all.reshape(N, T)
UU = u_all.reshape(N, T)
VV = v_all.reshape(N, T)
PP = p_all.reshape(N, T)

## Visualize PINN vs. reference flow field

In [11]:
def load_saved_model(num_layers, hidden_size, epochs, model, train_selection):
    """ 
    Params:
    hidden_size - int, # of hidden units for each neural network layer
    num_layers - int, # of neural network layers
    epochs - int, # of training epochs
    model - int, whether to use model 1 (Raissi 2019) or model 2 (continuity PDE)
    train_selection - float, frac of all data (N*T) to select for training OR 
                    'BC', select the boundary conditions for training (all timesteps)
    """
    nu = 0.01
    rho = 1

    # Instantiate model, load saved state_dict
    torch.manual_seed(0)
    if model == 1:
        PINN_model = NavierStokesPINN1(hidden_size=hidden_size, num_layers=num_layers, nu=nu, rho=rho)
    elif model ==2:
        PINN_model = NavierStokesPINN2(hidden_size=hidden_size, num_layers=num_layers, nu=nu, rho=rho)

    PINN_model.load_state_dict(torch.load(f'data/model{model}_{num_layers}l_{hidden_size}h_{epochs}e_{train_selection}d.pt'))
    PINN_model.eval() # Set model to evaluation mode
    return PINN_model

In [12]:
def plot_flow_field(model, title=''):
    """ 
    Params:
    PyTorch model to evaluate
    """
    fig, axes = plt.subplots(ncols = 2, nrows = 2, figsize=(10, 6), sharex=True, sharey=True)

    # Initial plot with first timestep
    model_output = model(XX[:, [0]], YY[:, [0]], TT[:, [0]]) # Get predictions at first timestep
    u_pred, v_pred, p_pred = model_output[0], model_output[1], model_output[2]
    # Convert to numpy
    u_pred, v_pred, p_pred = (u_pred.detach().numpy().flatten(), 
                            v_pred.detach().numpy().flatten(),
                            p_pred.detach().numpy().flatten())
    # Predicted velocity magnitude and pressure
    vel_pred = np.sqrt(u_pred ** 2 + v_pred ** 2)
    contour_vel_pred = axes[0, 0].contourf(vel_pred.reshape(50, 100), levels=30, cmap='jet')
    contour_p_pred = axes[0, 1].contourf(p_pred.reshape(50, 100), levels=30, cmap='jet')

    # Plot DNS reference
    vel = np.sqrt(UU[:, 0] ** 2 + VV[:, 0] ** 2) # velocity magnitude
    contour_vel = axes[1, 0].contourf(vel.reshape(50, 100), levels=30, cmap='jet')
    contour_p = axes[1, 1].contourf(PP[:, 0].reshape(50, 100), levels=30, cmap='jet')

    fig.colorbar(contour_vel, ax=[axes[0, 0], axes[1, 0]], orientation='vertical', shrink=0.45)
    fig.colorbar(contour_p, ax=[axes[0, 1], axes[1, 1]], orientation='vertical', shrink=0.45)

    # Animate future timesteps
    def animate(i):
        [ax.clear() for ax in axes.flatten()]
        # Get predictions
        model_output = model(XX[:, [i]], YY[:, [i]], TT[:, [i]])
        u_pred, v_pred, p_pred = model_output[0], model_output[1], model_output[2]
        # Convert to numpy
        u_pred, v_pred, p_pred = (u_pred.detach().numpy().flatten(), 
                                v_pred.detach().numpy().flatten(),
                                p_pred.detach().numpy().flatten())
        # Predicted velocity magnitude and pressure
        vel_pred = np.sqrt(u_pred ** 2 + v_pred ** 2)
        contour_vel_pred = axes[0, 0].contourf(vel_pred.reshape(50, 100), levels=30, cmap='jet')
        axes[0, 0].set_title('Predicted velocity magnitude')
        contour_p_pred = axes[0, 1].contourf(p_pred.reshape(50, 100), levels=30, cmap='jet')
        axes[0, 1].set_title('Predicted pressure')

        # Plot DNS reference
        vel = np.sqrt(UU[:, i] ** 2 + VV[:, i] ** 2) # velocity magnitude
        axes[1, 0].contourf(vel.reshape(50, 100), levels=30, cmap='jet')
        contour_vel = axes[1, 0].set_title('Reference velocity magnitude')
        axes[1, 1].contourf(PP[:, i].reshape(50, 100), levels=30, cmap='jet')
        contour_p = axes[1, 1].set_title('Reference pressure')

        fig.supxlabel(r'$x$')
        fig.supylabel(r'$y$')
        fig.suptitle(title)

    ani = animation.FuncAnimation(fig, animate, 20, interval=1, blit=False)
    return ani

### Model 2: 5 layers, 30 hidden units, 20000 epochs

In [5]:
# Load model
model2_5l_30h_20000e = load_saved_model(num_layers=5, hidden_size=30, epochs=20000, model=2, train_selection=0.005)

In [6]:
# Plot flow field
%matplotlib notebook
ani = plot_flow_field(model2_5l_30h_20000e)
ani.save('figures/ref_vs_pred_model2_5l_30h_20000e_0.005d.gif')
from IPython.display import HTML
HTML(ani.to_jshtml())

<IPython.core.display.Javascript object>

MovieWriter ffmpeg unavailable; using Pillow instead.


### Model 2: 5 layers, 30 hidden units, 50 epochs

In [17]:
# Load model
model2_5l_30h_50e = load_saved_model(num_layers=5, hidden_size=30, epochs=50, model=2, train_selection=0.005)

In [22]:
# Plot flow field
%matplotlib notebook
ani = plot_flow_field(model2_5l_30h_50e)
ani.save('figures/ref_vs_pred_model2_5l_30h_50e_0.005d.gif')
from IPython.display import HTML
HTML(ani.to_jshtml())

<IPython.core.display.Javascript object>

MovieWriter ffmpeg unavailable; using Pillow instead.
